In [ ]:
# Diabetic information
import pandas as pd
import numpy as np
import string
df = pd.read_csv('diabetic_data.csv', encoding='unicode_escape')
df = pd.DataFrame(df)
df.head(5)


#284 sample

encounter_id  patient_nbr             race  gender      age weight  \
0       2278392      8222157        Caucasian  Female   [0-10)      ?   
1        149190     55629189        Caucasian  Female  [10-20)      ?   
2         64410     86047875  AfricanAmerican  Female  [20-30)      ?   
3        500364     82442376        Caucasian    Male  [30-40)      ?   
4         16680     42519267        Caucasian    Male  [40-50)      ?   

   admission_type_id  discharge_disposition_id  admission_source_id  \
0                  6                        25                    1   
1                  1                         1                    7   
2                  1                         1                    7   
3                  1                         1                    7   
4                  1                         1                    7   

   time_in_hospital  ... citoglipton insulin  glyburide-metformin  \
0                 1  ...          No      No                   No   
1                 3  ...          No      Up                   No   
2                 2  ...          No      No                   No   
3                 2  ...          No      Up                   No   
4                 1  ...          No  Steady                   No   

   glipizide-metformin  glimepiride-pioglitazone  metformin-rosiglitazone  \
0                   No                        No                       No   
1                   No                        No                       No   
2                   No                        No                       No   
3                   No                        No                       No   
4                   No                        No                       No   

   metformin-pioglitazone  change diabetesMed readmitted  
0                      No      No          No         NO  
1                      No      Ch         Yes        >30  
2                      No      No         Yes         NO  
3                      No      Ch         Yes         NO  
4                      No      Ch         Yes         NO  

[5 rows x 50 columns]

In [ ]:
# 1. Melt: I want to know the information of '171311670' enconter_id in term of ['number_diagnoses','max_glu_serum','A1Cresult','time_in_hospital','diabetesMed','insulin','readmitted']]
# assign the general information of patient
melt_column = ['encounter_id','race','gender','age','insulin','change'] 
# assign the Value that I want to know
df_melted = df.melt(id_vars = melt_column, value_vars= ['number_diagnoses','max_glu_serum','A1Cresult','time_in_hospital','diabetesMed','insulin','readmitted']) 
df_melted[df_melted['encounter_id'] == 171311670]

encounter_id             race gender      age insulin change  \
61341      171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   
163107     171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   
264873     171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   
366639     171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   
468405     171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   
570171     171311670  AfricanAmerican   Male  [50-60)  Steady     Ch   

                variable value  
61341   number_diagnoses     9  
163107     max_glu_serum   NaN  
264873         A1Cresult   NaN  
366639  time_in_hospital     1  
468405       diabetesMed   Yes  
570171        readmitted    NO

In [ ]:
#2. Group by: After melted, I want to count all of the combined medication by gender
melt_column2 = ['encounter_id','race','gender','age','insulin','change'] 
df_melted2 = df.melt(id_vars= melt_column2, value_vars= ['glyburide-metformin','glipizide-metformin','glimepiride-pioglitazone','metformin-rosiglitazone','metformin-pioglitazone'], var_name= 'Combined Drug',value_name= 'status')
# choose the medicated drug by ignoring 'No' from the dataset
df_groupby = df_melted2[df_melted2['status'] != 'No'] 
df_groupby.groupby(['gender','Combined Drug','status'])['status'].count()

gender  Combined Drug             status
Female  glimepiride-pioglitazone  Steady      1
        glipizide-metformin       Steady      3
        glyburide-metformin       Down        4
                                  Steady    356
                                  Up          4
        metformin-pioglitazone    Steady      1
Male    glipizide-metformin       Steady     10
        glyburide-metformin       Down        2
                                  Steady    336
                                  Up          4
        metformin-rosiglitazone   Steady      2
Name: status, dtype: int64

In [ ]:
# 3. Aggregation :I want to know max, min, avg and std of ['time_in_hospital','num_medications','number_diagnoses','num_lab_procedures'] of diabetes patient 
# classified by age and gender (using group by to help reporting easyily)

df.groupby(['gender','age']).agg({
    'time_in_hospital': ['mean', 'std'],
    'num_medications': ['min', 'max','mean', 'std'],
    'number_diagnoses': ['min', 'max', 'mean', 'std'],
    'num_lab_procedures': ['min', 'max', 'mean', 'std']
})

time_in_hospital           num_medications      \
                                     mean       std             min max   
gender          age                                                       
Female          [0-10)           2.662651  1.212507               1  34   
                [10-20)          2.995025  2.253282               1  32   
                [20-30)          3.556553  2.518741               1  62   
                [30-40)          3.776133  2.626146               1  57   
                [40-50)          4.084182  2.875190               1  64   
                [50-60)          4.186421  2.909920               1  70   
                [60-70)          4.474912  3.000818               1  75   
                [70-80)          4.688809  3.051542               1  68   
                [80-90)          4.879125  3.020559               1  65   
                [90-100)         4.775836  2.880604               1  41   
Male            [0-10)           2.423077  1.334062               1  19   
                [10-20)          3.463668  3.025280               1  34   
                [20-30)          3.581952  2.607859               1  65   
                [30-40)          3.831370  2.769935               1  63   
                [40-50)          3.995691  2.900954               1  68   
                [50-60)          4.065868  2.924170               1  79   
                [60-70)          4.292794  3.003339               1  81   
                [70-80)          4.477527  3.032797               1  74   
                [80-90)          4.697695  3.044679               1  61   
                [90-100)         4.705063  2.821311               1  42   
Unknown/Invalid [60-70)          1.000000       NaN               6   6   
                [70-80)          4.500000  4.949747              21  22   

                                              number_diagnoses                \
                               mean       std              min max      mean   
gender          age                                                            
Female          [0-10)     6.807229  4.694205                1   8  2.939759   
                [10-20)    8.256219  5.169113                1   9  4.067164   
                [20-30)   12.425494  6.880335                1  14  5.933573   
                [30-40)   14.460685  7.231069                1  16  6.524977   
                [40-50)   15.950946  7.912416                1  16  7.024527   
                [50-60)   16.899207  8.228825                1  16  7.234718   
                [60-70)   17.399060  8.385052                1  16  7.511708   
                [70-80)   16.566750  7.835808                1  16  7.604147   
                [80-90)   15.489586  7.075758                1  16  7.873134   
                [90-100)  13.982526  6.188368                3  14  7.879181   
Male            [0-10)     5.512821  3.152997                1   9  2.435897   
                [10-20)    8.307958  5.619161                1   9  3.782007   
                [20-30)   11.044199  6.883444                1   9  5.729282   
                [30-40)   13.597024  8.083776                1  16  6.356479   
                [40-50)   14.838326  8.037806                1  13  6.874025   
                [50-60)   16.273837  8.953132                1  16  7.242400   
                [60-70)   16.910603  8.874873                1  16  7.501532   
                [70-80)   16.222995  8.285056                2  16  7.707143   
                [80-90)   15.070338  7.121720                2  16  7.913200   
                [90-100)  13.408861  6.446124                1  10  7.898734   
Unknown/Invalid [60-70)    6.000000       NaN                5   5  5.000000   
                [70-80)   21.500000  0.707107                4   9  6.500000   

                                   num_lab_procedures                  \
                               std                min  max       mean   
ge

In [ ]:
# 4. Pivot: I want to pivot the mean of [['time_in_hospital','num_medications']] with the race and gender 
# I put 'race' as a index, and 'gender' as a column while the values are time_in_hospital and num_medications
df_pivoted = df.pivot_table(index=['race',], columns='gender', values=['time_in_hospital','num_medications'],aggfunc= 'mean')
df_pivoted.reset_index(inplace=True)

df_pivoted

race num_medications                             \
gender                           Female       Male Unknown/Invalid   
0                     ?       15.744925  15.885764            13.5   
1       AfricanAmerican       15.634465  14.952686             NaN   
2                 Asian       13.198113  13.383901             NaN   
3             Caucasian       16.464335  16.091046             NaN   
4              Hispanic       14.216117  13.815873             NaN   
5                 Other       15.017380  15.343461            22.0   

       time_in_hospital                            
gender           Female      Male Unknown/Invalid  
0              4.429832  4.149385             4.5  
1              4.541269  4.455493             NaN  
2              3.899371  4.089783             NaN  
3              4.481443  4.281379             NaN  
4              4.086081  4.029630             NaN  
5              4.252674  4.298547             1.0

In [137]:
# 5. iterable: identify the medical specialty of each patient
df_medspe_notnull = df.loc[df['medical_specialty'] != '?'] # filter not null off the dataframe

df_medspe_notnull_melt = df_medspe_notnull.melt(id_vars = 'encounter_id', value_vars= 'medical_specialty') # melt to make the df accessible
df_medspe_notnull_melt.head(10) # for checking the filter

for idx, row in df_medspe_notnull_melt.iterrows(): # iterate the dataframe 
   print(f"Patient number {row['encounter_id']} have a medical specialty from '{row['value']}' department")



Patient number 2278392 have a medical specialty from 'Pediatrics-Endocrinology' department
Patient number 15738 have a medical specialty from 'InternalMedicine' department
Patient number 40926 have a medical specialty from 'Family/GeneralPractice' department
Patient number 42570 have a medical specialty from 'Family/GeneralPractice' department
Patient number 84222 have a medical specialty from 'Cardiology' department
Patient number 236316 have a medical specialty from 'Cardiology' department
Patient number 248916 have a medical specialty from 'Surgery-General' department
Patient number 252822 have a medical specialty from 'Cardiology' department
Patient number 260166 have a medical specialty from 'Family/GeneralPractice' department
Patient number 325848 have a medical specialty from 'Cardiology' department
Patient number 383430 have a medical specialty from 'Cardiology' department
Patient number 449142 have a medical specialty from 'Family/GeneralPractice' department
Patient number 486